In [1]:
from collections import defaultdict

import nltk
from transformers import BertTokenizerFast, BertForTokenClassification, Trainer, TrainingArguments
from datasets import load_from_disk, concatenate_datasets
import torch
import lib
import numpy as np
import evaluate
import seqeval
from transformers import GenerationConfig

In [2]:

dataset_full = load_from_disk('full_invalid_dataset_sentence-1952522')

In [2]:
device = 'cpu'
if torch.cuda.is_available():
    device = 'cuda'
    print('Cuda')

Cuda


In [3]:
num_labels = len(lib.id2label)
max_length = 64

gen_config = GenerationConfig(max_length=max_length)

tokenizer = BertTokenizerFast.from_pretrained('bert-large-uncased')
model = BertForTokenClassification.from_pretrained('trained_bert_model_full_data_modified', num_labels=num_labels)

new_tokens = ['[MATH]', '[DISPLAY]', '[ITALIC]']
num_added_tokens = tokenizer.add_tokens(new_tokens)

model.resize_token_embeddings(len(tokenizer))

model.to(device)
batch_size = 256

In [5]:
def create_pos_batch(token_lists):
    padded_input_ids = [tokenizer.convert_tokens_to_ids(['[CLS]'] + tokens[0:62] + ['[SEP]']) + [0] * (max_length - (len(tokens) +2)) for tokens in token_lists]
    input_ids_tensor = torch.tensor(padded_input_ids, device=device)
    attention_mask = torch.tensor([[1]*(min(len(tokens) + 2, 64)) + [0]*(max_length - (len(tokens) + 2)) for tokens in token_lists], device=device)
    
    inputs = {
        "input_ids": input_ids_tensor,
        "attention_mask": attention_mask
    }
    
    with torch.no_grad():
        logits = model(**inputs).logits
    
    predicted_labels_batch = torch.argmax(logits, dim=2)
    
    return [[lib.id2label[label.item()] for label in sequence if label != -100] for sequence in predicted_labels_batch]

labels_list = []
tokens_list = []

from tqdm.notebook import tqdm

batches_per_batch = 40

iterator2 = range(0, len(dataset_full['tokens']), batch_size*batches_per_batch)

In [6]:
for j in tqdm(iterator2, total=len(iterator2), desc='Resizing'):
    print(j, j + batches_per_batch*batch_size - 1)
    dataset = dataset_full.select(range(j, min(j + batches_per_batch*batch_size - 1, len(dataset_full))))
    iterator1 = range(0, len(dataset['tokens']), batch_size)
    
    for i in tqdm(iterator1, total=len(iterator1), desc='Processing Rows'):
        batch_tokens = dataset['tokens'][i:i + batch_size]
        labels_list.extend(create_pos_batch(batch_tokens))
        tokens_list.extend(batch_tokens)

Resizing:   0%|          | 0/191 [00:00<?, ?it/s]

0 10239


Processing Rows:   0%|          | 0/40 [00:00<?, ?it/s]

10240 20479


Processing Rows:   0%|          | 0/40 [00:00<?, ?it/s]

...

Processing Rows:   0%|          | 0/40 [00:00<?, ?it/s]

1935360 1945599


Processing Rows:   0%|          | 0/40 [00:00<?, ?it/s]

1945600 1955839


Processing Rows:   0%|          | 0/28 [00:00<?, ?it/s]

In [7]:
token_to_label = []

for token, label in zip(tokens_list, labels_list):
    token_to_label.append([(t, l) for t, l in zip(token, label)])



In [8]:
import pandas as pd
from datasets import Dataset

df = pd.DataFrame({'toks': tokens_list, 'predicted_labels': labels_list, 'token_to_label': token_to_label})
res = Dataset.from_pandas(df)

In [9]:
res.save_to_disk('full_large_model_predicted_data')

Saving the dataset (0/5 shards):   0%|          | 0/1952332 [00:00<?, ? examples/s]

In [4]:
from datasets import load_from_disk
dataset = load_from_disk(f'full_large_model_predicted_data')

In [5]:
len(dataset)

1952332

In [3]:
len(dataset['toks'][0])

34

In [6]:
def update_tokens(row):
    length = len(row['toks']) + 2
    row['toks'] = ['[CLS]'] + row['toks'][0:62] + ['[SEP]']
    return row


dataset = dataset.map(update_tokens)

In [5]:
len(dataset['toks'][0])

36

In [6]:
len(dataset['predicted_labels'][0])

64

In [7]:
def update_token_to_label(row):
    row['token_to_label'] = [(t, l) for t, l in zip(row['toks'], row['predicted_labels'])]
    return row
        
dataset = dataset.map(update_token_to_label)


In [8]:
token_to_label = dataset['token_to_label']

In [ ]:
dataset['token_to_label'][0]

In [9]:
dict_math_labels = defaultdict(int)
dict_display_label = defaultdict(int)
dict_italic_label = defaultdict(int)
for token_label_arr in token_to_label:
    for token, label in token_label_arr:
        if token == "[MATH]":
            dict_math_labels[label] += 1
        elif token == "[DISPLAY]":
            dict_display_label[label] += 1
        elif token == "[ITALIC]":
            dict_italic_label[label] += 1


In [10]:
def to_latex(token_list):
    s = str(token_list)
    s = s.replace("[", "")
    s = s.replace("]", "")
    s = s.replace("('", "")
    s = s.replace("),", "\\\\ \n")
    s = s.replace("',", " &")
    s = s.replace(")", "")
    return s

In [11]:
math_labels = dict_math_labels.items()
math_total = 0
for key, value in math_labels:
    math_total += value

print(math_total)
print(to_latex(sorted(math_labels, key=lambda x: x[1], reverse=True)))


4437657
NOUN & 1957137\\ 
 ADJ & 1920963\\ 
 VERB & 493526\\ 
 PROPN & 62691\\ 
 INTJ & 1677\\ 
 ADV & 1439\\ 
 AUX & 146\\ 
 NUM & 67\\ 
 PRON & 4\\ 
 PUNCT & 4\\ 
 PART & 3


In [12]:
display_labels = dict_display_label.items()
display_total = 0
for key, value in display_labels:
    display_total += value

print(display_total)

print(to_latex(sorted(display_labels, key=lambda x: x[1], reverse=True)))

722174
NOUN & 479226\\ 
 ADJ & 127220\\ 
 VERB & 92748\\ 
 PROPN & 19963\\ 
 ADV & 979\\ 
 CCONJ & 775\\ 
 SCONJ & 396\\ 
 PUNCT & 239\\ 
 PRON & 200\\ 
 DET & 131\\ 
 AUX & 127\\ 
 ADP & 85\\ 
 INTJ & 78\\ 
 NUM & 5\\ 
 PART & 2


In [13]:
italic_labels = dict_italic_label.items()
italics_total = 0
for key, value in italic_labels:
    italics_total += value

print(italics_total)

print(to_latex(sorted(italic_labels, key=lambda x: x[1], reverse=True)))

1051831
NOUN & 947115\\ 
 PROPN & 52425\\ 
 ADJ & 45084\\ 
 VERB & 4714\\ 
 ADV & 1499\\ 
 SYM & 901\\ 
 PRON & 53\\ 
 NUM & 13\\ 
 PART & 11\\ 
 INTJ & 5\\ 
 CCONJ & 4\\ 
 AUX & 4\\ 
 SCONJ & 3


In [14]:
def sum_all_labels(standard_dict, other_dict):
    for key, value in other_dict.items():
        standard_dict[key] += value

In [15]:
full_dict = defaultdict(int)
sum_all_labels(full_dict, dict_math_labels)
sum_all_labels(full_dict, dict_display_label)
sum_all_labels(full_dict, dict_italic_label)
full_labels = full_dict.items()
print(to_latex(sorted(full_labels, key=lambda x: x[1], reverse=True)))

NOUN & 3383478\\ 
 ADJ & 2093267\\ 
 VERB & 590988\\ 
 PROPN & 135079\\ 
 ADV & 3917\\ 
 INTJ & 1760\\ 
 SYM & 901\\ 
 CCONJ & 779\\ 
 SCONJ & 399\\ 
 AUX & 277\\ 
 PRON & 257\\ 
 PUNCT & 243\\ 
 DET & 131\\ 
 NUM & 85\\ 
 ADP & 85\\ 
 PART & 16


In [ ]:
adjectives = defaultdict(int)

for token_label_arr in token_to_label:
    for token, label in token_label_arr:
        if label in ['ADJ']:
            adjectives[token] += 1
        
            
        

In [ ]:
adjectives

In [23]:
adjectives_dict = lambda: defaultdict(list)
adjectives_seperated_math = defaultdict(adjectives_dict)
adjectives_seperated_display = defaultdict(adjectives_dict)
adjectives_seperated_italic = defaultdict(adjectives_dict)

for token_label_arr in token_to_label:
    for i, (token, label) in enumerate(token_label_arr):
        
        if token == '[MATH]' and label == 'NOUN':
            before = token_label_arr[max(i-3, 0):i]
            for t, label in before:
                if label in ['ADJ']:
                    adjectives_seperated_math[i][label].append(t)
                    
        if token == '[DISPLAY]' and label == 'NOUN':
            before = token_label_arr[max(i-3, 0):i]
            for t, label in before:
                if label in ['ADJ']:
                    adjectives_seperated_display[i][label].append(t)
                    
        if token == '[ITALIC]' and label == 'NOUN':
            before = token_label_arr[max(i-3, 0):i]
            for t, label in before:
                if label in ['ADJ']:
                    adjectives_seperated_display[i][label].append(t)

In [24]:
adjectives_seperated_math

defaultdict(<function __main__.<lambda>()>,
            {6: defaultdict(list,
                         {'ADJ': ['-cluster',
                           '[MATH]',
                           'morphism',
                           '[MATH]',
                           '[MATH]',
                           'morphism',
                           '[MATH]',
                           'constant',
                           'simple',
                           'simple',
                           'separable',
                           'invariable',
                           'covariant',
                           'covariant',
                           'pythagorean',
                           'ideal',
                           'ideal',
                           'such',
                           '[MATH]',
                           'such',
                           '[MATH]',
                           'such',
                           'such',
                           'same',
             

In [25]:
adjectives_seperated_display

defaultdict(<function __main__.<lambda>()>,
            {22: defaultdict(list,
                         {'ADJ': ['acyclic',
                           'separable',
                           'non-zero',
                           'proper',
                           'constant',
                           'many',
                           'many',
                           '[MATH]',
                           '[MATH]',
                           'eigenvalue',
                           '[MATH]',
                           '[MATH]',
                           '[MATH]',
                           '[MATH]',
                           '[MATH]',
                           '[MATH]',
                           'linear',
                           'linear',
                           'parabolic',
                           'parabolic',
                           'nonzero',
                           'greater',
                           'greater',
                           'proper',
         